# Implementacion del algoritmo CLR

> Recomendaciones
* Para las variables binarias no se requiere hacer codificacion one - hot
* Probar con el regresor ElasticNet y verificar si efectivanete elimina variables colineales en cada grupo.
* Investigar un regresor que elimine la colinealidad entre variables.
* Modificar el concepto de error promedio aceptado.
* Modificar el numero minimo de regristros por grupo, al menor el 10% de los datos, registros minimos.
* Seleccionar un error promedio aceptado Correcto.

In [2]:
# Dependencias
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn import model_selection
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import Lasso
from sklearn.linear_model import ElasticNet
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import ElasticNet
from math import sqrt
from sklearn.metrics import r2_score
from sklearn.linear_model import LassoCV
from numpy import mean
from numpy import std
from numpy import arange
from numpy import absolute
from pandas import read_csv
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedKFold

In [3]:
# Cargue de los datos | informacion
df = pd.read_excel("../Archivos Generados/DatasetFinal.xlsx")

In [4]:
# Se muestra los primeros 5 elementos
df.head(5)

ID_LOTE TIPO_SIEMBRA SEM_TRATADAS MATERIAL_GENETICO CULT_ANT DRENAJE  \
0       40   Mecanizado           NO     PIONEER 30F32  Algodon      SI   
1       43   Mecanizado           SI            DK 234     Maiz      SI   
2       44   Mecanizado           NO     PIONEER 30F32  Algodon      SI   
3       45   Mecanizado           NO              Otro  Algodon      SI   
4       46   Mecanizado           NO              Otro  Algodon      SI   

  METODO_COSECHA ALMACENAMIENTO_FINCA  DIAS_EN_EMERGER  \
0         Manual                   NO                5   
1         Manual                   NO                5   
2         Manual                   NO                5   
3         Manual                   NO                5   
4         Manual                   NO                5   

   DIAS_EN_EMERGER_A_FLORECER  ...  Temp_Max_Avg_Mad  Temp_Min_Avg_Mad  \
0                          63  ...             32.05             23.60   
1                          64  ...             32.37             23.49   
2                          59  ...             32.17             23.53   
3                          64  ...             32.19             23.54   
4                          63  ...             32.19             23.54   

   Temp_Avg_Mad  Diurnal_Range_Avg_Mad  Sol_Ener_Accu_Mad  \
0         27.83                   8.45           13197.57   
1         27.93                   8.89           12436.49   
2         27.85                   8.63           11267.17   
3         27.86                   8.65           11066.68   
4         27.86                   8.65           11066.68   

   Temp_Max_34_Freq_Mad  Rain_Accu_Mad  Rain_10_Freq_Mad  Rhum_Avg_Mad  \
0                  0.05          279.3              0.23         82.41   
1                  0.03          221.2              0.26         81.86   
2                  0.03          226.0              0.27         82.61   
3                  0.03          223.2              0.29         81.84   
4                  0.03          223.2              0.29         81.84   

   RDT_AJUSTADO  
0       4767.44  
1       4651.16  
2       5180.23  
3       4897.67  
4       5302.33  

[5 rows x 116 columns]

In [5]:
# Selección de las variables categoricas
cat_features = df.select_dtypes(include = ["object", "category"]).columns
print("Cantidad de variables categoricas: ", len(cat_features))
cat_features

Cantidad de variables categoricas:  30


Index(['TIPO_SIEMBRA', 'SEM_TRATADAS', 'MATERIAL_GENETICO', 'CULT_ANT',
       'DRENAJE', 'METODO_COSECHA', 'ALMACENAMIENTO_FINCA',
       'TERRENO_CIRCUN_RASTA', 'POSICION_PERFIL_RASTA', 'PEDREG_PERFIL_ROCAS',
       'CAP_ENDURE_RASTA', 'MOTEADOS_RASTA', 'MOTEADOS_MAS70cm._RASTA',
       'ESTRUCTURA_RASTA', 'OBSERVA_EROSION_RASTA', 'OBSERVA_MOHO_RASTA',
       'OBSERVA_COSTRAS_DURAS_RASTA', 'SITIO_EXPUESTO_SOL_RASTA',
       'OBSERVA_COSTRAS_BLANCAS_RASTA', 'OBSERVA_COSTAS_NEGRAS_RASTA',
       'REGION_SECA_ARIDA_RASTA', 'OBSERVA_RAICES_VIVAS_RASTA',
       'OBSERVA_PLANTAS_PEQUENAS_RASTA', 'OBSERVA_HOJARASCA_MO_RASTA',
       'SUELO_NEGRO_BLANDO_RASTA', 'CUCHILLO_PRIMER_HTE_RASTA',
       'CERCA_RIOS_QUEBRADAS_RASTA', 'RECUBRIMIENTO_VEGETAL__SUELO_RASTA',
       'd.interno', 'drenaje_externo'],
      dtype='object')

In [6]:
# Seleccion de variables Binarias.
bin_features =['SEM_TRATADAS','DRENAJE','ALMACENAMIENTO_FINCA','CAP_ENDURE_RASTA','MOTEADOS_RASTA','MOTEADOS_MAS70cm._RASTA',
               'OBSERVA_EROSION_RASTA','OBSERVA_MOHO_RASTA','OBSERVA_RAICES_VIVAS_RASTA','OBSERVA_HOJARASCA_MO_RASTA',
                'SUELO_NEGRO_BLANDO_RASTA','CUCHILLO_PRIMER_HTE_RASTA','CERCA_RIOS_QUEBRADAS_RASTA',
               ]
print("Cantidad de variables binarias: ",len(bin_features))               

Cantidad de variables binarias:  13


In [7]:
# Codificacion Dataset de caracteristicas binarias
bin_dataset = df[bin_features].replace({'SI': 1, 'NO': 0})

In [9]:
# Visualizacion Dataset de caracteristicas binarias
bin_dataset.head(5)

SEM_TRATADAS  DRENAJE  ALMACENAMIENTO_FINCA  CAP_ENDURE_RASTA  \
0             0        1                     0                 0   
1             1        1                     0                 1   
2             0        1                     0                 1   
3             0        1                     0                 1   
4             0        1                     0                 1   

   MOTEADOS_RASTA  MOTEADOS_MAS70cm._RASTA  OBSERVA_EROSION_RASTA  \
0               1                        0                      0   
1               1                        0                      0   
2               1                        0                      0   
3               1                        0                      0   
4               1                        0                      0   

   OBSERVA_MOHO_RASTA  OBSERVA_RAICES_VIVAS_RASTA  OBSERVA_HOJARASCA_MO_RASTA  \
0                   0                           0                           0   
1                   0                           0                           1   
2                   0                           1                           1   
3                   0                           0                           1   
4                   0                           0                           1   

   SUELO_NEGRO_BLANDO_RASTA  CUCHILLO_PRIMER_HTE_RASTA  \
0                         0                          1   
1                         0                          1   
2                         0                          1   
3                         0                          0   
4                         0                          0   

   CERCA_RIOS_QUEBRADAS_RASTA  
0                           0  
1                           0  
2                           0  
3                           0  
4                           0

In [10]:
# Longitud de las variables categoricas
len(cat_features)
# Se eliminar variables binarias de la lista de categoricas.
categorical_features = [x for x in cat_features if x not in bin_features]
print("variables Categoricas", len(categorical_features))

variables Categoricas 17


In [11]:
categorical_features

['TIPO_SIEMBRA',
 'MATERIAL_GENETICO',
 'CULT_ANT',
 'METODO_COSECHA',
 'TERRENO_CIRCUN_RASTA',
 'POSICION_PERFIL_RASTA',
 'PEDREG_PERFIL_ROCAS',
 'ESTRUCTURA_RASTA',
 'OBSERVA_COSTRAS_DURAS_RASTA',
 'SITIO_EXPUESTO_SOL_RASTA',
 'OBSERVA_COSTRAS_BLANCAS_RASTA',
 'OBSERVA_COSTAS_NEGRAS_RASTA',
 'REGION_SECA_ARIDA_RASTA',
 'OBSERVA_PLANTAS_PEQUENAS_RASTA',
 'RECUBRIMIENTO_VEGETAL__SUELO_RASTA',
 'd.interno',
 'drenaje_externo']

In [12]:
df["d.interno"].value_counts()

BUENO                465
LENTO A MUY LENTO    333
EXCESIVO               1
Name: d.interno, dtype: int64

In [13]:
# Codificación dummy de las variables categoricas
df_cat = pd.get_dummies(df[categorical_features])
df_cat.tail()

TIPO_SIEMBRA_Manual  TIPO_SIEMBRA_Mecanizado  \
794                    0                        1   
795                    1                        0   
796                    1                        0   
797                    1                        0   
798                    0                        1   

     MATERIAL_GENETICO_ADV 9293 (Syngenta)  \
794                                      0   
795                                      0   
796                                      0   
797                                      0   
798                                      0   

     MATERIAL_GENETICO_ADV 9339 (Syngenta)  MATERIAL_GENETICO_CORPOICA V 114  \
794                                      0                                 0   
795                                      0                                 0   
796                                      0                                 0   
797                                      0                                 0   
798                                      0                                 0   

     MATERIAL_GENETICO_Cerato (Syngenta)  MATERIAL_GENETICO_DK 1040  \
794                                    0                          0   
795                                    0                          0   
796                                    0                          0   
797                                    0                          0   
798                                    0                          0   

     MATERIAL_GENETICO_DK 1596  MATERIAL_GENETICO_DK 234  \
794                          0                         0   
795                          0                         0   
796                          0                         0   
797                          0                         0   
798                          0                         0   

     MATERIAL_GENETICO_DK 234 YGRR  ...  \
794                              0  ...   
795                              0  ...   
796                              0  ...   
797                              0  ...   
798                              1  ...   

     RECUBRIMIENTO_VEGETAL__SUELO_RASTA_BUENO  \
794                                         0   
795                                         1   
796                                         0   
797                                         0   
798                                         0   

     RECUBRIMIENTO_VEGETAL__SUELO_RASTA_ESPACIADO  \
794                                             0   
795                                             0   
796                                             0   
797                                             0   
798                                             0   

     RECUBRIMIENTO_VEGETAL__SUELO_RASTA_MUY BUENO  \
794                                             0   
795                                             0   
796                                             0   
797                                             0   
798                                             0   

     RECUBRIMIENTO_VEGETAL__SUELO_RASTA_REGULAR  \
794                                           1   
795                                           0   
796                                           1   
797                                           1   
798                                           1   

     RECUBRIMIENTO_VEGETAL__SUELO_RASTA_SIN COBERTURA  d.interno_BUENO  \
794                                                 0                1   
795                                                 0                1   
796                                                 0                1   
797                                                 0                1   
798                                                 0                1   

     d.interno_EXCESIVO  d.interno_LENTO A MUY LENTO  drenaje_externo_LENTO  \
794                   0                            0                      1   
795                   0               

In [14]:
# Se eliminan las variables categoricas  del dataframe principal y se mantienen unicamente las variables numericas
df.drop(cat_features, axis = 1, inplace = True)

In [15]:
df.columns

Index(['ID_LOTE', 'DIAS_EN_EMERGER', 'DIAS_EN_EMERGER_A_FLORECER',
       'DIAS_EN_FLORECER_A_COSECHAR', 'POBLACION_20DIAS_AJT', 'ALTURA_LOT',
       'ContEnfQui_Emer_Flor', 'ContEnfQui_Flor_Cose', 'ContMalMec_Siem_Emer',
       'ContMalMec_Emer_Flor', 'ContMalMec_Flor_Cose', 'ContMalQui_Antes_Siem',
       'ContMalQui_Siem_Emer', 'ContMalQui_Emer_Flor', 'ContMalQui_Flor_Cose',
       'ContPlaQui_Antes_Siem', 'ContPlaQui_Siem_Emer', 'ContPlaQui_Emer_Flor',
       'ContPlaQui_Flor_Cose', 'TotN_Antes_Siem', 'TotN_Siem_Emer',
       'TotN_Emer_Flor', 'TotP_Antes_Siem', 'TotP_Siem_Emer', 'TotP_Emer_Flor',
       'TotK_Antes_Siem', 'TotK_Siem_Emer', 'TotK_Emer_Flor',
       'FerOrg_Emer_Flor', 'FerQui_Antes_Siem', 'FerQui_Siem_Emer',
       'FerQui_Emer_Flor', 'PENDIENTE_RASTA', 'NO_CAPAS_RASTA', 'PH_RASTA',
       'PROFUND_CAP_ENDURE_RASTA', 'ESPESOR_CAP_ENDURE_RASTA',
       'PROFUND_MOTEADOS_RASTA', 'PROFUND_RAICES_VIVAS_RASTA', 'prof_efectiva',
       'Porc_A', 'Porc_Ar', 'Porc_ArA', 'P

In [16]:
# Se construye un unico dataset | vista minable con valores numericos
# Se unen 3 dataset (Variables Categoricas | Variables binarias | variables numericas)
df_final = pd.concat([df,df_cat,bin_dataset ], axis = 1)

In [17]:
df_final

ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0         40                5                          63   
1         43                5                          64   
2         44                5                          59   
3         45                5                          64   
4         46                5                          63   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             68                 60000          13   
1                             63                 60000          15   
2                             66                 60000          12   
3                             59                 60000          12   
4                             60                 60000          16   
..                           ...                   ...         ...   
794                           84                 70000          18   
795                           81                 62000          16   
796                           79                 61000          17   
797                           95                 65000          17   
798                           83                 60000          19   

     ContEnfQui_Emer_Flor  ContEnfQui_Flor_Cose  ContMalMec_Siem_Emer  \
0                       0                     0                     0   
1                       0                     0                     0   
2                       0                     0                     0   
3                       0                     0                     0   
4                       0                     0                     0   
..                    ...                   ...                   ...   
794                     0                     0                     0   
795                     0                     0                     0   
796                     0                     0                     0   
797                     0                     0                     0   
798                     0                     0                     0   

     ContMalMec_Emer_Flor  ...  CAP_ENDURE_RASTA  MOTEADOS_RASTA  \
0                       0  ...                 0               1   
1                       0  ...                 1               1   
2                       0  ...                 1               1   
3                       0  ...                 1               1   
4                       0  ...                 1               1   
..                    ...  ...               ...             ...   
794                     0  ...                 0               0   
795                     0  ...                 0               0   
796                     0  ...                 0               0   
797                     0  ...                 0               0   
798                     0  ...                 1               0   

     MOTEADOS_MAS70cm._RASTA  OBSERVA_EROSION_RASTA  OBSERVA_MOHO_RASTA  \
0                          0                      0                   0   
1                          0                      0                   0   
2                          0                      0                   0   
3                          0                      0                   0   
4                          0                      0                   0   
..                       ...                    ...                 ...   
794                        0                      0                   0   
795                        0                      0                   0   
796                        0                      0           

In [19]:
# Division de los datos | variables dependientes
# X: Dependiente
# Y: Independiente
Y = df_final.RDT_AJUSTADO
X = df_final.drop(["RDT_AJUSTADO","ID_LOTE"], axis=1)

In [20]:
# Se deviden los datos en conjunto de entranmiento y test
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.20, random_state=40)
print(X_train.shape); print(X_test.shape)


(639, 174)
(160, 174)


# Modelado

## Implementacion de la red Elasticnet

* ElasticNet se caracteriza porque incliye penalizacion L1 Y L2

In [21]:
# define model
model = ElasticNet(alpha=1.0, l1_ratio=0.5)
# define model evaluation method
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=1)
# evaluate model
scores = cross_val_score(model, X, Y, scoring='neg_mean_absolute_error', cv=cv, n_jobs=-1)
# force scores to be positive
scores = absolute(scores)
print("Scores: ", scores)
print('Mean MAE: %.3f (%.3f)' % (mean(scores), std(scores)))

Scores:  [760.01015496 734.03287976 686.61061501 604.56887933 648.68689666
 615.29725778 824.08057106 735.17374846 736.22945901 647.94359046
 595.79823956 642.71364899 757.25596127 634.00019189 720.09047728
 816.44398521 757.67663612 762.63428435 707.94003106 689.43520322
 768.11317652 671.38948679 741.39319575 691.5735824  760.48723611
 680.76808789 708.40242235 642.23938144 686.126512   744.58629074]
Mean MAE: 705.723 (58.750)


In [22]:
# Teniendo en cuenta el MAE se ajusta un modelo bajo esta regresión
# Se define el modelo
modelEN = ElasticNet(alpha=1.0, l1_ratio=0.5)
# fit model
modelEN.fit(X_train, y_train)
# make a prediction
yhat = modelEN.predict(X_test)
# summarize prediction
print('Predicted:', yhat)


Predicted: [4047.45526851 4135.63305632 5616.501863   6303.28215324 3877.46211766
 3188.54516201 3788.56139104 5601.01430462 3692.0766884  4373.47125051
 4708.95334115 6534.86166298 4807.01853949 2738.97803812 3701.29928796
 3591.04475741 3767.55188518 2903.36020619 3195.22608014 3720.18857682
 5861.46845693 4740.20888376 3187.39009895 3196.64304512 6208.5823408
 6514.57106745 4918.51311055 5620.7256993  4784.54512039 5148.23836885
 2459.56534962 4443.80569505 4335.92654424 2314.39179587 5991.7603703
 5704.08644064 4608.44392997 4587.91942185 3862.2732973  4750.9292154
 4482.42860193 4559.60100669 4576.72434293 4579.10523597 3968.29774699
 3851.83900509 4760.33745723 4129.58299184 5292.42084024 6174.14982447
 4113.83234861 3430.16404294 4809.44744755 4963.86237826 2527.77862607
 5621.51531793 5245.43991641 4391.41051131 4839.30265087 5457.82121018
 5851.24136789 4498.88023199 4338.08493609 5990.99407743 6313.76924156
 4614.74203852 4223.45455191 5965.50876896 4688.85885357 5970.6220634

C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.754e+08, tolerance: 1.223e+05
  model = cd_fast.enet_coordinate_descent(


In [23]:
# Coeficiente de determinacion de la predicción
R_2 = modelEN.score(X_train, y_train)
print("El ajuste del modelo (Training ) es : ", R_2)
# Se calcula el error deel modelo
# Calculo del error 
print("======================= Conjunto de test ==========================")
print("MSE: ", (mean_squared_error(y_test,yhat,squared=False)))
print("MAE", mean_absolute_error(y_test,yhat))
print("r**2: ", r2_score(y_test, yhat))

El ajuste del modelo (Training ) es :  0.652311597920004
======================= Conjunto de test ==========================
MSE:  957.9504977329331
MAE 760.7848771462761
r**2:  0.5271055084826309


In [24]:
# Caracteristicas del modelo ajustado con Regresion Lineal Lasso
# Coeficientes del modelo ajustado..
modelEN.coef_
# intercepto de la funcion de desicion
modelEN.intercept_
# Cantidad de caracteristicas seleccionadas (Variables independientes)
modelEN.n_features_in_
# Nombre de los atributos | caracteristicas seleccionadas
#modelEN.feature_names_in_


174

### Ajuste de Hiperparametros (alpha Y l1_ratio) | Obtención del mejor modelo

In [25]:
# Dependencias
from sklearn.linear_model import ElasticNetCV
# define model evaluation method
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=1)
# define model
ratios = arange(0, 1, 0.01)
alphas = [1e-5, 1e-4, 1e-3, 1e-2, 1e-1, 0.0, 1.0, 10.0, 100.0]
model = ElasticNetCV(l1_ratio=ratios, alphas=alphas, cv=cv, n_jobs=-1)
# fit model
model.fit(X, Y)
# summarize chosen configuration
print('alpha: %f' % model.alpha_)
print('l1_ratio_: %f' % model.l1_ratio_)


C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:617: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:617: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:617: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 331542309.00635374, tolerance: 135797.19253151235
  model = cd_fast.enet_coordinate_descent_gram(
C:\Users\German\AppData\Roaming\Python\Python38\site-pa

alpha: 0.100000
l1_ratio_: 0.970000


C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.906e+07, tolerance: 1.533e+05
  model = cd_fast.enet_coordinate_descent(


### Mejores parametros encontrados.
* alpha: 0.1
* li_ratio:0.97


# IMPLMENTACIÓN DEL ENFOQUE CLUSTERWISE

## FASE #1 : Distribución de los datos

In [26]:
# Variables de entrada
# Dataset
DataSet = df_final.copy()
# Minimo numero de registros que debe tener cada grupo aceptado  | Criterio del 10% de registros aceptados
MinimoRegistros = 80
# Error promedio aceptado de los grupos , permite seleccionar los grupos que mas se ajusten al modelo de RL
# Valor obtenido del proceso de ajuste con CV utilizando el regresor ridge
#ErrorPromedioAceptado = 658.08
# Valor de tolerancia al error c/d vez que se crea el siguiente grupo | puede ser un grilla de diferentes valores a tolerar
ErrorPromedioAdicional = 20
# Coeficiente de correlación minimo aceptado por c/d grupo
CoeficienteCorrelacionMinimo = 0.88
# Lista de grupos aceptados
GruposAceptados = []
# Modelos aceptados x c/d grupo con sus atributos y valores de correlación
modelosAceptados = []
# Registros huerfanos que no fueron aceptados en ningun grupo
huerfanos = []
# Maximo valor de MAR permitido para conformar cada grupo
MAE_Permitido = 45



In [27]:
DataSet


ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0         40                5                          63   
1         43                5                          64   
2         44                5                          59   
3         45                5                          64   
4         46                5                          63   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             68                 60000          13   
1                             63                 60000          15   
2                             66                 60000          12   
3                             59                 60000          12   
4                             60                 60000          16   
..                           ...                   ...         ...   
794                           84                 70000          18   
795                           81                 62000          16   
796                           79                 61000          17   
797                           95                 65000          17   
798                           83                 60000          19   

     ContEnfQui_Emer_Flor  ContEnfQui_Flor_Cose  ContMalMec_Siem_Emer  \
0                       0                     0                     0   
1                       0                     0                     0   
2                       0                     0                     0   
3                       0                     0                     0   
4                       0                     0                     0   
..                    ...                   ...                   ...   
794                     0                     0                     0   
795                     0                     0                     0   
796                     0                     0                     0   
797                     0                     0                     0   
798                     0                     0                     0   

     ContMalMec_Emer_Flor  ...  CAP_ENDURE_RASTA  MOTEADOS_RASTA  \
0                       0  ...                 0               1   
1                       0  ...                 1               1   
2                       0  ...                 1               1   
3                       0  ...                 1               1   
4                       0  ...                 1               1   
..                    ...  ...               ...             ...   
794                     0  ...                 0               0   
795                     0  ...                 0               0   
796                     0  ...                 0               0   
797                     0  ...                 0               0   
798                     0  ...                 1               0   

     MOTEADOS_MAS70cm._RASTA  OBSERVA_EROSION_RASTA  OBSERVA_MOHO_RASTA  \
0                          0                      0                   0   
1                          0                      0                   0   
2                          0                      0                   0   
3                          0                      0                   0   
4                          0                      0                   0   
..                       ...                    ...                 ...   
794                        0                      0                   0   
795                        0                      0                   0   
796                        0                      0           

In [28]:
# Calcular modelo de regresion lineal para todo el datset.
# Antes de entrar a la funcion asegurase que se a realizo la respectiva transformacion, codificacion , normalización de la data.
def calcularModeloRegresionLineal(DataSet):
    # Division de los datos
    # Variables dependientes | independiente
    Y = DataSet.RDT_AJUSTADO
    X = DataSet.drop(["RDT_AJUSTADO","ID_LOTE"], axis=1)
    # Se define el modelo de regresion con ElasticNet | o el mejor regresor seleccionado.
    # Se realiza la implmentacion del regresor ElasticNet (alpha=0.1, l1_ratio=0.97) con la mejor configuracion seleccionada.
    modelElasticNet = ElasticNet(alpha=0.1, l1_ratio=0.97)
    # fit model
    model = modelElasticNet.fit(X,Y)
    # Obtengo el ajuste del modelo
    r_2 = model.score(X,Y)
    #print(r_2)
    # Retorna del modelo y el coeficiente de determinacion del modelo
    return [model, r_2]


In [29]:
# Funcion para ordenar los datos deacuerdo al error de predicción
# Entrada: Dataset, modelo, errorPromedioAceptado
# Salida: Dataset ordenado
def OrdenarDatosPorErrorDePrediccion(Dataset, model):
    # Se dividen los datos
    # X:  Variables independendientes
    # Y:  Variables dependientes.
    Y = Dataset.RDT_AJUSTADO
    X = Dataset.drop(["RDT_AJUSTADO","ID_LOTE"], axis=1)
    # Se realizan las predicciones del modelo
    yhat = model.predict(X)
    Dataset["Yhat"] = pd.Series(yhat)
    # Calculo del error absoluto para ca/d registro
    Dataset["EA"] = abs(Dataset.RDT_AJUSTADO - Dataset.Yhat)
    # Se calcula la columa para el error promomedio aceptado
    #Dataset["EPA"] = calcularErroPromedioAceptado(Dataset)
    # Se ordena los registros de [menor a mayor] , tomando referencia el valor absoluto
    DataSetOrdenado = Dataset.sort_values(by=['EA'],ascending=True)
    #DataSetOrdenado["EPA"] = calcularErroPromedioAceptado(DataSetOrdenado)
    
    # Se retorna el datset ordenado
    return  DataSetOrdenado 
    

In [30]:
mr1, r_2 = calcularModeloRegresionLineal(DataSet)
print("El ajuste del modelo es: ", r_2)

El ajuste del modelo es:  0.7420467584701328


C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.906e+07, tolerance: 1.533e+05
  model = cd_fast.enet_coordinate_descent(


In [31]:
def calcularErroPromedioAceptado(DataSet):
    EPA = 0
    Acumulador = 0
    ErrorPromedioAceptado = []
    for i in range(len(DataSet)):
        #print("Iteracion: ", i)
        Acumulador = Acumulador + DataSet.loc[i].EA
        EPA = Acumulador/(i+1)
        #print("Error: ", EPA)
        #ErrorPromedioAceptado.insert(DataSet.index[i], EPA)
        ErrorPromedioAceptado.append(EPA)
    
    serie = pd.Series(ErrorPromedioAceptado)
    return serie


In [32]:
DataSet

ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0         40                5                          63   
1         43                5                          64   
2         44                5                          59   
3         45                5                          64   
4         46                5                          63   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             68                 60000          13   
1                             63                 60000          15   
2                             66                 60000          12   
3                             59                 60000          12   
4                             60                 60000          16   
..                           ...                   ...         ...   
794                           84                 70000          18   
795                           81                 62000          16   
796                           79                 61000          17   
797                           95                 65000          17   
798                           83                 60000          19   

     ContEnfQui_Emer_Flor  ContEnfQui_Flor_Cose  ContMalMec_Siem_Emer  \
0                       0                     0                     0   
1                       0                     0                     0   
2                       0                     0                     0   
3                       0                     0                     0   
4                       0                     0                     0   
..                    ...                   ...                   ...   
794                     0                     0                     0   
795                     0                     0                     0   
796                     0                     0                     0   
797                     0                     0                     0   
798                     0                     0                     0   

     ContMalMec_Emer_Flor  ...  CAP_ENDURE_RASTA  MOTEADOS_RASTA  \
0                       0  ...                 0               1   
1                       0  ...                 1               1   
2                       0  ...                 1               1   
3                       0  ...                 1               1   
4                       0  ...                 1               1   
..                    ...  ...               ...             ...   
794                     0  ...                 0               0   
795                     0  ...                 0               0   
796                     0  ...                 0               0   
797                     0  ...                 0               0   
798                     0  ...                 1               0   

     MOTEADOS_MAS70cm._RASTA  OBSERVA_EROSION_RASTA  OBSERVA_MOHO_RASTA  \
0                          0                      0                   0   
1                          0                      0                   0   
2                          0                      0                   0   
3                          0                      0                   0   
4                          0                      0                   0   
..                       ...                    ...                 ...   
794                        0                      0                   0   
795                        0                      0                   0   
796                        0                      0           

In [34]:
datasetOrd = OrdenarDatosPorErrorDePrediccion(DataSet,mr1)

In [43]:
datasetOrdenado = datasetOrd.reset_index()

In [36]:
# Guardamos el dataset ordenado en un archivo excel
datasetOrdenado.reset_index().to_excel("../Archivos Generados/Dataset_ordendo_MAE.xlsx")

In [37]:
# FUncion que permite crear el grupo con las mejores intancias que cumplan con lso criterios de aceptacion.
# - Mejor error absoluto
# - Numero de registros aceptado x grupo
def CrearGrupo(DataSetOrdenado):
    RegistrosAceptados = []
    for x in range(len(DataSetOrdenado)):
        if DataSetOrdenado.loc[x].EA <= DataSetOrdenado.loc[x].EPA:
            RegistrosAceptados.append(DataSetOrdenado.loc[x])

        else:
            print("Entra aqui")
            #break
    
    # Registros que conforman n-grupos
    # Cada Grupo va ser un sub-dataset 
    return RegistrosAceptados

In [38]:
datasetOrdenado

index  ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0      326     2481                6                          45   
1      384     2660                5                          54   
2      480     3018                4                          48   
3      311     2450                5                          47   
4      319     2465                5                          47   
..     ...      ...              ...                         ...   
794    527     3631                4                          46   
795    462     2950                4                          47   
796    170     1985                5                          46   
797    360     2612                6                          40   
798     99     1827                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             77                 54000          11   
1                             80                 60000          10   
2                             82                 55000          12   
3                             73                 70000          72   
4                             81                 67000          14   
..                           ...                   ...         ...   
794                           85                 65000           5   
795                           87                 55000           4   
796                           76                 75000           7   
797                           82                 72000          18   
798                           70                 70000          12   

     ContEnfQui_Emer_Flor  ContEnfQui_Flor_Cose  ContMalMec_Siem_Emer  ...  \
0                       0                     0                     0  ...   
1                       0                     0                     0  ...   
2                       1                     0                     0  ...   
3                       1                     0                     0  ...   
4                       1                     0                     0  ...   
..                    ...                   ...                   ...  ...   
794                     0                     0                     0  ...   
795                     0                     0                     0  ...   
796                     0                     0                     0  ...   
797                     0                     0                     0  ...   
798                     0                     0                     0  ...   

     MOTEADOS_MAS70cm._RASTA  OBSERVA_EROSION_RASTA  OBSERVA_MOHO_RASTA  \
0                          0                      0                   0   
1                          0                      0                   0   
2                          0                      0                   0   
3                          0                      0                   0   
4                          0                      0                   0   
..                       ...                    ...                 ...   
794                        0                      0                   0   
795                        0                      0                   0   
796                        0                      0                   0   
797                        0                      0                   0   
798                        0                      0                   0   

     OBSERVA_RAICES_VIVAS_RASTA  OBSERVA_HOJARASCA_MO_RASTA  \
0                             1                           0   
1                             1                           0   
2                             1                           0   
3                             1                           0   
4                             1                           1   
..                          ...                         ...   
794                           1                           0   
795  

In [45]:
DataSetOrdenado = calcularMAE(datasetOrdenado)

In [46]:
DataSetOrdenado.to_excel("../Archivos Generados/MAE.xlsx")

In [53]:
DataSetOrdenado.RDT_AJUSTADO

0      3813.95
1      4000.00
2      4958.14
3      4409.30
4      4834.88
        ...   
794    2637.21
795    1158.14
796    6312.09
797    1674.42
798    1032.56
Name: RDT_AJUSTADO, Length: 799, dtype: float64

In [51]:
# FUncion que permite crear el grupo con las mejores intancias que cumplan con lso criterios de aceptacion.
# - Mejor error absoluto
# - Numero de registros aceptado x grupo
# crear el grupo
Selected = datasetOrdenado.loc[datasetOrdenado.EPA < MAE_Permitido]

In [39]:
def LimpiezaColumnasDataframe(DataFrameGrupo):
    # Se eliminan algunas variables del Grupo 
    varEliminar = ["Yhat","EA"]
    DataFrameGrupo = DataFrameGrupo.drop(varEliminar,axis=1)
    # Se retorna el grupo
    return DataFrameGrupo
    
    

In [40]:
def EliminarRegistrosGrupo(Grupo):
    # Borrar del datset original las observaciones seleccionadas en cada grupo
    #indexEliminar = list(Grupo.index)
    indexEliminar = list(Grupo["index"])
    #print("Longitud Dataset Original")
    df_nuevo = DataSet[DataSet.index.isin(indexEliminar)== False]
    # Se retorna el
    return df_nuevo
    

In [41]:
# Funcion para calcular el MAE de cada registro
def calcularMAE(dataset):
    dataset["EPA"] = calcularErroPromedioAceptado(dataset)
    return dataset

In [56]:
DataSetOr

ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
739     4271                5                          48   
741     4273                6                          49   
236     2201                3                          50   
37       672                7                          39   
93      1820                3                          46   
..       ...              ...                         ...   
359     2611                6                          44   
462     2950                4                          47   
360     2612                6                          40   
99      1827                4                          49   
170     1985                5                          46   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
739                           81                 66700          17   
741                           84                 65750          17   
236                           78                 55000           9   
37                           113                 64000          14   
93                            88                 70000          10   
..                           ...                   ...         ...   
359                           81                 58000          18   
462                           87                 55000           4   
360                           82                 72000          18   
99                            70                 70000          12   
170                           76                 75000           7   

     ContEnfQui_Emer_Flor  ContEnfQui_Flor_Cose  ContMalMec_Siem_Emer  \
739                     0                     0                     0   
741                     0                     0                     0   
236                     0                     0                     0   
37                      0                     0                     0   
93                      0                     0                     0   
..                    ...                   ...                   ...   
359                     1                     0                     0   
462                     0                     0                     0   
360                     0                     0                     0   
99                      0                     0                     0   
170                     0                     0                     0   

     ContMalMec_Emer_Flor  ...  MOTEADOS_MAS70cm._RASTA  \
739                     0  ...                        0   
741                     0  ...                        0   
236                     0  ...                        0   
37                      0  ...                        0   
93                      0  ...                        1   
..                    ...  ...                      ...   
359                     0  ...                        0   
462                     0  ...                        0   
360                     0  ...                        0   
99                      0  ...                        0   
170                     0  ...                        0   

     OBSERVA_EROSION_RASTA  OBSERVA_MOHO_RASTA  OBSERVA_RAICES_VIVAS_RASTA  \
739                      0                   0                           1   
741                      0                   0                           1   
236                      0                   0                           1   
37                       0                   0                           1   
93                       0                   0                           1   
..                     ...                 ...                         ...   
359                      0                   0                           1   
462                      0                   0                           1   
360                      0                   0                           1   
99                       0                   0                   

In [42]:
# Implementacion del Algoritmo.
contador = 0
while(len(DataSet) != 0):
    contador = contador+1
    print(DataSet)
    # 1. Calcular modelo de regresion dataset completo.
    modelrr, cd_r = calcularModeloRegresionLineal(DataSet)
    # 2. Seleccion de las mejores intancias (Dataset Ordenado)
    DataSetOr = OrdenarDatosPorErrorDePrediccion(DataSet, modelrr)
    datasetOrdenado = DataSetOr.reset_index()
    print("Ordenado: ",datasetOrdenado)
    # 3. Calculo del MAE
    DatasetOrdenado = calcularMAE(datasetOrdenado)
    print("MAE", DatasetOrdenado)
    # 3. Crear Grupo con las mejores instancias.
    grupo = DatasetOrdenado.loc[DatasetOrdenado.EPA < MAE_Permitido]
    print(len(grupo))
    #print("Cantidad de registros por grupo: ",Grupo.shape)
    if (len(grupo) > MinimoRegistros):
        # 4. Eliminar variables 
        Grupo = LimpiezaColumnasDataframe(grupo)
        DataSet = LimpiezaColumnasDataframe(DataSet)
        #print("Cantidad registos aceptados: ", Grupo.shape)
        #print("Longitud Dataset Original 3: ", DataSet.shape)
        # 5. Calculamos modelo de regresion Lineal para el grupo
        ModeloGrupo, R_2 = calcularModeloRegresionLineal(Grupo)
        # 6. Se evalua las condiciones del Coef Determinacion
        if (R_2 > CoeficienteCorrelacionMinimo):
            # 7. Se agregan el grupo y el modelo a las respectivas listas
            GruposAceptados.append(Grupo)
            modelosAceptados.append(ModeloGrupo)
            Grupo.to_excel(f"../Archivos Generados/Grupo{contador}.xlsx")
            # 8. Se Eliminan las instancias del df original para la proxim
            # a iteracion
            DataSet = EliminarRegistrosGrupo(Grupo)
            # 9. Se adiciona el error promedio aceptado.
            MAE_Permitido= MAE_Permitido + ErrorPromedioAdicional
    else:
        # Salir del bucle
        Huerfanos = DataSet
        print("Logitud Huerfanos: ", Huerfanos.shape)
        Huerfanos.to_excel("../Archivos Generados/Huerfanos.xlsx")
        break


     ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0         40                5                          63   
1         43                5                          64   
2         44                5                          59   
3         45                5                          64   
4         46                5                          63   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             68                 60000          13   
1                             63                 60000          15   
2                             66                 60000   

C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.074e+07, tolerance: 1.533e+05
  model = cd_fast.enet_coordinate_descent(


Ordenado:       index  ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0      739     4271                5                          48   
1      741     4273                6                          49   
2      236     2201                3                          50   
3       37      672                7                          39   
4       93     1820                3                          46   
..     ...      ...              ...                         ...   
794    359     2611                6                          44   
795    462     2950                4                          47   
796    360     2612                6                          40   
797     99     1827                4                          49   
798    170     1985                5                          46   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             81                 66700          17   
1                             84

C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.785e+05, tolerance: 9.601e+03
  model = cd_fast.enet_coordinate_descent(


     ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0         40                5                          63   
1         43                5                          64   
3         45                5                          64   
4         46                5                          63   
5         47                6                          72   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             68                 60000          13   
1                             63                 60000          15   
3                             59                 60000   

...

MAE      index  ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0      248     2213                4                          46   
1      303     2438                5                          47   
2      109     1881                5                          50   
3      118     1899                4                          46   
4      426     2909                5                          46   
..     ...      ...              ...                         ...   
578    794     4378                7                          47   
579    795     4379                5                          47   
580    796     4380                6                          49   
581    797     4382                7                          48   
582    798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             81                 55000           8   
1                             66       

C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.152e+06, tolerance: 1.216e+04
  model = cd_fast.enet_coordinate_descent(


     ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
4         46                5                          63   
10       271                6                          56   
11       272                5                          43   
15       277                5                          68   
16       278                6                          65   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
4                             60                 60000          16   
10                            72                 60000          10   
11                            85                 60000   

C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.544e+07, tolerance: 1.145e+05
  model = cd_fast.enet_coordinate_descent(


MAE      index  ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0      205     2053                3                          46   
1      104     1833                4                          49   
2      258     2275                6                          47   
3       45      690                4                          43   
4      184     2009                5                          47   
..     ...      ...              ...                         ...   
472    794     4378                7                          47   
473    795     4379                5                          47   
474    796     4380                6                          49   
475    797     4382                7                          48   
476    798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             84                 60000          13   
1                             78       

In [52]:
print("Caractristicas Grupo 1: ", modelosAceptados[0].n_features_in_)
print("Caractristicas Grupo 2: ", modelosAceptados[1].n_features_in_)
print("Caractristicas Grupo 3: ", modelosAceptados[2].n_features_in_)

Caractristicas Grupo 1:  176
Caractristicas Grupo 2:  176
Caractristicas Grupo 3:  176


In [ ]:
# Implementacion del Algoritmo.
while(len(DataSet) != 0):
    print(DataSet)
    # 1. Calcular modelo de regresion dataset completo.
    modelrr, cd_r = calcularModeloRegresionLineal(DataSet)
    # 2. Seleccion de las mejores intancias (Dataset Ordenado)
    DataSetOr = OrdenarDatosPorErrorDePrediccion(DataSet, modelrr)
    #print(len(DataSetOr))
    # 3. Crear Grupo con las mejores instancias.
    Grupo = pd.DataFrame(CrearGrupo(DataSetOr))
    #print("Cantidad de registros por grupo: ",Grupo.shape)
    if (len(Grupo) > MinimoRegistros):
        # 4. Eliminar variables 
        Grupo = LimpiezaColumnasDataframe(Grupo)
        DataSet = LimpiezaColumnasDataframe(DataSet)
        #print("Cantidad registos aceptados: ", Grupo.shape)
        #print("Longitud Dataset Original 3: ", DataSet.shape)
        # 5. Calculamos modelo de regresion Lineal para el grupo
        ModeloGrupo, R_2 = calcularModeloRegresionLineal(Grupo)
        # 6. Se evalua las condiciones del Coef Determinacion
        if (R_2 > CoeficienteCorrelacionMinimo):
            # 7. Se agregan el grupo y el modelo a las respectivas listas
            GruposAceptados.append(Grupo)
            modelosAceptados.append(ModeloGrupo)
            # 8. Se Eliminan las instancias del df original para la proxim
            # a iteracion
            DataSet = EliminarRegistrosGrupo(Grupo)
            # 9. Se adiciona el error promedio aceptado.
            ErrorPromedioAceptado = ErrorPromedioAceptado + ErrorPromedioAdicional
    else:
        # Salir del bucle
        Huerfanos = DataSet
        print("Logitud Huerfanos: ", Huerfanos.shape)
        break

    


     ID_LOTE  DIAS_EN_EMERGER  DIAS_EN_EMERGER_A_FLORECER  \
0         40                5                          63   
1         43                5                          64   
2         44                5                          59   
3         45                5                          64   
4         46                5                          63   
..       ...              ...                         ...   
794     4378                7                          47   
795     4379                5                          47   
796     4380                6                          49   
797     4382                7                          48   
798     4432                4                          49   

     DIAS_EN_FLORECER_A_COSECHAR  POBLACION_20DIAS_AJT  ALTURA_LOT  \
0                             68                 60000          13   
1                             63                 60000          15   
2                             66                 60000   

C:\Users\German\AppData\Roaming\Python\Python38\site-packages\sklearn\linear_model\_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.074e+07, tolerance: 1.533e+05
  model = cd_fast.enet_coordinate_descent(


AttributeError: 'Series' object has no attribute 'EPA'

<te>